In [1]:
!pip install pyspark


Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.1.2 -> 24.1.2
[notice] To update, run: python3 -m pip install --upgrade pip


In [2]:
from pyspark.sql import SparkSession

In [3]:
sessao_spark = SparkSession.builder\
                .appName("Recomendador PySpark")\
                .getOrCreate()
sessao_spark

24/07/22 12:06:25 WARN Utils: Your hostname, Gustavo-PC resolves to a loopback address: 127.0.1.1; using 192.168.31.75 instead (on interface enp4s0)
24/07/22 12:06:25 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/07/22 12:06:25 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [4]:
from pyspark import SparkFiles

In [5]:
url_dados = 'https://github.com/IgorNascAlves/dados/blob/main/dados_musicas.csv?raw=true'
sessao_spark.sparkContext.addFile(url_dados)
path_dados_file = 'file://' + SparkFiles.get('dados_musicas.csv')

In [6]:
dados = sessao_spark.read.csv(
    path_dados_file,
    header=True,
    sep=';',
    inferSchema=True
)

In [7]:
dados.show()

+------------------+----+------------+--------------+------------------+-----------+------------------+--------+--------------------+--------------------+---+--------+-------------------+----+--------------------+----------+-----------+------------------+--------------------+
|           valence|year|acousticness|       artists|      danceability|duration_ms|            energy|explicit|                  id|    instrumentalness|key|liveness|           loudness|mode|                name|popularity|speechiness|             tempo|        artists_song|
+------------------+----+------------+--------------+------------------+-----------+------------------+--------+--------------------+--------------------+---+--------+-------------------+----+--------------------+----------+-----------+------------------+--------------------+
|             0.285|2000|     0.00239|      Coldplay|             0.429|     266773|0.6609999999999999|       0|3AJwUDP919kvQ9Qco...|             1.21E-4| 11|   0.234|  

In [8]:
dados.printSchema()

root
 |-- valence: double (nullable = true)
 |-- year: integer (nullable = true)
 |-- acousticness: double (nullable = true)
 |-- artists: string (nullable = true)
 |-- danceability: double (nullable = true)
 |-- duration_ms: integer (nullable = true)
 |-- energy: double (nullable = true)
 |-- explicit: integer (nullable = true)
 |-- id: string (nullable = true)
 |-- instrumentalness: double (nullable = true)
 |-- key: integer (nullable = true)
 |-- liveness: double (nullable = true)
 |-- loudness: double (nullable = true)
 |-- mode: integer (nullable = true)
 |-- name: string (nullable = true)
 |-- popularity: integer (nullable = true)
 |-- speechiness: double (nullable = true)
 |-- tempo: double (nullable = true)
 |-- artists_song: string (nullable = true)



In [9]:
dados.count()

20311

In [10]:
len(dados.columns)

19

In [11]:
import pyspark.sql.functions as f

In [12]:
dados.select([f.count(f.when(f.isnull(c), 1)).alias(c) for c in dados.columns]).show()

+-------+----+------------+-------+------------+-----------+------+--------+---+----------------+---+--------+--------+----+----+----------+-----------+-----+------------+
|valence|year|acousticness|artists|danceability|duration_ms|energy|explicit| id|instrumentalness|key|liveness|loudness|mode|name|popularity|speechiness|tempo|artists_song|
+-------+----+------------+-------+------------+-----------+------+--------+---+----------------+---+--------+--------+----+----+----------+-----------+-----+------------+
|      0|   0|           0|      0|           0|          0|     0|       0|  0|               0|  0|       0|       0|   0|   0|         0|          0|    0|           0|
+-------+----+------------+-------+------------+-----------+------+--------+---+----------------+---+--------+--------+----+----+----------+-----------+-----+------------+



In [13]:
print(sorted(dados.select('year').distinct().collect()))

[Row(year=2000), Row(year=2001), Row(year=2002), Row(year=2003), Row(year=2004), Row(year=2005), Row(year=2006), Row(year=2007), Row(year=2008), Row(year=2009), Row(year=2010), Row(year=2011), Row(year=2012), Row(year=2013), Row(year=2014), Row(year=2015), Row(year=2016), Row(year=2017), Row(year=2018), Row(year=2019), Row(year=2020)]


In [14]:
url_anos_dados = 'https://github.com/IgorNascAlves/dados/blob/main/dados_musicas_ano.csv?raw=true'

sessao_spark.sparkContext.addFile(url_anos_dados)
path_dados_file = 'file://' + SparkFiles.get('dados_musicas_ano.csv')

dados_anos = sessao_spark.read.csv(path_dados_file,
                                   header=True,
                                   inferSchema=True)

In [15]:
dados_anos.show()

+----+----+------------------+-------------------+------------------+-------------------+-------------------+-------------------+-------------------+-------------------+------------------+-------------------+-------------------+---+
|mode|year|      acousticness|       danceability|       duration_ms|             energy|   instrumentalness|           liveness|           loudness|        speechiness|             tempo|            valence|         popularity|key|
+----+----+------------------+-------------------+------------------+-------------------+-------------------+-------------------+-------------------+-------------------+------------------+-------------------+-------------------+---+
|   1|1921|0.8868960000000005| 0.4185973333333336|260537.16666666663|0.23181513333333334|0.34487805886666656|            0.20571| -17.04866666666665|           0.073662|101.53149333333329|0.37932666666666665| 0.6533333333333333|  2|
|   1|1922|0.9385915492957748| 0.4820422535211267|165469.74647887325

In [16]:
dados_anos = dados_anos.filter('year >= 2000')
dados_anos.show()

+----+----+-------------------+------------------+------------------+------------------+-------------------+-------------------+-------------------+-------------------+------------------+------------------+------------------+---+
|mode|year|       acousticness|      danceability|       duration_ms|            energy|   instrumentalness|           liveness|           loudness|        speechiness|             tempo|           valence|        popularity|key|
+----+----+-------------------+------------------+------------------+------------------+-------------------+-------------------+-------------------+-------------------+------------------+------------------+------------------+---+
|   1|2000|0.28932270051635994| 0.590918047034764| 242724.6426380368|0.6254128323108387|0.10116776879345596| 0.1976860429447853| -8.247765848670758|0.08920541922290394| 118.9993231083843|0.5594754601226991|  46.6840490797546|  7|
|   1|2001| 0.2868424748428934|0.5833178553615969|240307.79600997505|0.626985522

In [17]:
dados_anos.count()

21

In [18]:
len(dados_anos.columns)

14

In [19]:
!pip install plotly

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.1.2 -> 24.1.2
[notice] To update, run: python3 -m pip install --upgrade pip


In [20]:
import plotly.express as px

fig = px.line(dados_anos.toPandas(), 
              x='year', 
              y='loudness', 
              markers=True, 
              title='Variacao do loudness conforme os anos')
fig.show()

In [21]:
import plotly.graph_objects as go

fig = go.Figure()

temp = dados_anos.toPandas()

fig.add_trace(go.Scatter(x=temp['year'], y=temp['acousticness'], 
                    name='Acousticness'))
fig.add_trace(go.Scatter(x=temp['year'], y=temp['valence'],
                    name='Valence'))
fig.add_trace(go.Scatter(x=temp['year'], y=temp['danceability'],
                    name='Danceability'))
fig.add_trace(go.Scatter(x=temp['year'], y=temp['energy'],
                    name='Energy'))
fig.add_trace(go.Scatter(x=temp['year'], y=temp['instrumentalness'],
                    name='Instrumentalness'))
fig.add_trace(go.Scatter(x=temp['year'], y=temp['liveness'],
                    name='Liveness'))
fig.add_trace(go.Scatter(x=temp['year'], y=temp['speechiness'],
                    name='Speechiness'))

fig.show()


In [22]:
fig = px.imshow(dados_anos.drop('mode').toPandas().corr(),
                text_auto=True)
fig.show()

In [23]:
url_dados_generos = 'https://github.com/IgorNascAlves/dados/blob/main/dados_musicas_genero.csv?raw=true'

sessao_spark.sparkContext.addFile(url_dados_generos)
path_dados_file = 'file://' + SparkFiles.get('dados_musicas_genero.csv')

dados_generos = sessao_spark.read.csv(path_dados_file,
                                     header=True,
                                     inferSchema=True)

In [24]:

display(dados_generos.toPandas())

mode                  genres  acousticness  danceability   duration_ms  \
0        1  21st century classical      0.979333      0.162883  1.602977e+05   
1        1                   432hz      0.494780      0.299333  1.048887e+06   
2        1                   8-bit      0.762000      0.712000  1.151770e+05   
3        1                      []      0.651417      0.529093  2.328809e+05   
4        1              a cappella      0.676557      0.538961  1.906285e+05   
...    ...                     ...           ...           ...           ...   
2968     1                    zolo      0.222625      0.547082  2.580991e+05   
2969     0                 zouglou      0.161000      0.863000  2.063200e+05   
2970     1                    zouk      0.263261      0.748889  3.060728e+05   
2971     0            zurich indie      0.993000      0.705667  1.984173e+05   
2972     1                  zydeco      0.421038      0.629409  1.716717e+05   

        energy  instrumentalness  liveness   loudness  speechiness  \
0     0.071317          0.606834  0.361600 -31.514333     0.040567   
1     0.450678          0.477762  0.131000 -16.854000     0.076817   
2     0.818000          0.876000  0.126000  -9.180000     0.047000   
3     0.419146          0.205309  0.218696 -12.288965     0.107872   
4     0.316434          0.003003  0.172254 -12.479387     0.082851   
...        ...               ...       ...        ...          ...   
2968  0.610240          0.143872  0.204206 -11.295878     0.061088   
2969  0.909000          0.000000  0.108000  -5.985000     0.081300   
2970  0.622444          0.257227  0.089678 -10.289222     0.038778   
2971  0.172667          0.468633  0.179667 -11.453333     0.348667   
2972  0.609369          0.019248  0.255877  -9.854825     0.050491   

           tempo   valence  popularity  key  
0      75.336500  0.103783   27.833333    6  
1     120.285667  0.221750   52.500000    5  
2     133.444000  0.975000   48.000000    7  
3     112.857352  0.513604   20.859882    7  
4     112.110362  0.448249   45.820071    7  
...          ...       ...         ...  ...  
2968  125.494919  0.596155   33.778943    9  
2969  119.038000  0.845000   58.000000    7  
2970  101.965222  0.824111   46.666667    5  
2971   91.278000  0.739000    0.000000    7  
2972  126.366087  0.808544   30.261905    7  

[2973 rows x 14 columns]

In [25]:
dados_generos.count()

2973

In [26]:
dados_generos.select('genres').distinct().count()

2973

In [27]:
len(dados_generos.columns)

14

In [28]:
from pyspark.ml.feature import VectorAssembler

In [29]:
dados_generos.columns

['mode',
 'genres',
 'acousticness',
 'danceability',
 'duration_ms',
 'energy',
 'instrumentalness',
 'liveness',
 'loudness',
 'speechiness',
 'tempo',
 'valence',
 'popularity',
 'key']

In [30]:
x = dados_generos.columns
x.remove('genres')
x

['mode',
 'acousticness',
 'danceability',
 'duration_ms',
 'energy',
 'instrumentalness',
 'liveness',
 'loudness',
 'speechiness',
 'tempo',
 'valence',
 'popularity',
 'key']

In [31]:
dados_generos_vector = VectorAssembler(inputCols=x, 
                                       outputCol='features'
                                      ).transform(dados_generos).select(['features', 'genres'])

In [32]:
dados_generos_vector.show(truncate=False, n=5)

+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+----------------------+
|features                                                                                                                                                                                                                   |genres                |
+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+----------------------+
|[1.0,0.9793333333333332,0.16288333333333335,160297.66666666663,0.07131666666666665,0.60683367,0.3616,-31.514333333333337,0.04056666666666667,75.3365,0.10378333333333334,27.83333333333333,6.0]                            |21st century classical|
|[1.0,0.49478,0.2993

24/07/22 12:06:47 WARN package: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


In [33]:
from pyspark.ml.feature import StandardScaler

In [34]:
scaler = StandardScaler(inputCol='features',
                        outputCol='scaled_features')
scaler_model = scaler.fit(dados_generos_vector)
dados_generos_scaler = scaler_model.transform(dados_generos_vector)

In [35]:
dados_generos_scaler.show()

+--------------------+--------------------+--------------------+
|            features|              genres|     scaled_features|
+--------------------+--------------------+--------------------+
|[1.0,0.9793333333...|21st century clas...|[2.68174831000279...|
|[1.0,0.49478,0.29...|               432hz|[2.68174831000279...|
|[1.0,0.762,0.7120...|               8-bit|[2.68174831000279...|
|[1.0,0.6514170195...|                  []|[2.68174831000279...|
|[1.0,0.6765573049...|          a cappella|[2.68174831000279...|
|[1.0,0.45921,0.51...|            abstract|[2.68174831000279...|
|[1.0,0.3421466666...|      abstract beats|[2.68174831000279...|
|[1.0,0.2438540633...|    abstract hip hop|[2.68174831000279...|
|[0.0,0.3229999999...|           accordeon|[0.0,1.0101313736...|
|[1.0,0.446125,0.6...|           accordion|[2.68174831000279...|
|[0.0,0.0679505384...|          acid house|[0.0,0.2125045534...|
|[1.0,0.2569145079...|           acid rock|[2.68174831000279...|
|[1.0,0.00683,0.66...|   

In [36]:
from pyspark.ml.feature import PCA

In [37]:
pca = PCA(k=2,
          inputCol='scaled_features',
         outputCol='pca_features')
model_pca = pca.fit(dados_generos_scaler)
dados_generos_pca = model_pca.transform(dados_generos_scaler)

In [38]:
dados_generos_pca.select('pca_features').show(truncate=False)

+-----------------------------------------+
|pca_features                             |
+-----------------------------------------+
|[-2.507095366888566,-0.43816913737698426]|
|[0.5969679056633481,-4.9816120527513545] |
|[4.158460276223561,0.8366525081079923]   |
|[2.3873448785122164,0.4877989015663364]  |
|[2.6501218371679087,0.5756819768820428]  |
|[1.4965091203367626,-1.8644183183717817] |
|[3.9235207721573238,-0.2851835002352867] |
|[4.6110111098311135,0.6783790472312343]  |
|[2.8376900630842297,0.5712993716580531]  |
|[2.7066901398927827,1.2593788079708268]  |
|[4.698331383924287,-1.2765569680619442]  |
|[3.3759874966798673,-0.7560741064307506] |
|[5.608998877066021,-1.042731164439324]   |
|[-0.2954946352117681,0.27638645862362693]|
|[2.5725591062870423,1.3169815431109755]  |
|[3.400822802049345,-0.5073029625781933]  |
|[4.366720316263418,0.3364827059771049]   |
|[2.7254698167724003,-0.5058604987046399] |
|[4.958112358381604,-1.2627579957290722]  |
|[3.6934951846422712,-1.38227620

In [39]:
from pyspark.ml import Pipeline

In [40]:
pca_pipeline = Pipeline(stages=[VectorAssembler(inputCols=x, 
                                outputCol='features'),
                                StandardScaler(inputCol='features',
                                outputCol='scaled_features'),
                                PCA(k=2,inputCol='scaled_features',
                                outputCol='pca_features')])

In [41]:
pca_pipeline_model = pca_pipeline.fit(dados_generos)

In [42]:
dados_generos_pca = pca_pipeline_model.transform(dados_generos)

In [43]:
dados_generos_pca.show()

+----+--------------------+-------------------+-------------------+------------------+-------------------+--------------------+-------------------+-------------------+--------------------+------------------+-------------------+------------------+---+--------------------+--------------------+--------------------+
|mode|              genres|       acousticness|       danceability|       duration_ms|             energy|    instrumentalness|           liveness|           loudness|         speechiness|             tempo|            valence|        popularity|key|            features|     scaled_features|        pca_features|
+----+--------------------+-------------------+-------------------+------------------+-------------------+--------------------+-------------------+-------------------+--------------------+------------------+-------------------+------------------+---+--------------------+--------------------+--------------------+
|   1|21st century clas...| 0.9793333333333332|0.162883333

In [44]:
dados_generos_pca.select('pca_features').show(truncate=False)

+-----------------------------------------+
|pca_features                             |
+-----------------------------------------+
|[-2.507095366888566,-0.43816913737698426]|
|[0.5969679056633481,-4.9816120527513545] |
|[4.158460276223561,0.8366525081079923]   |
|[2.3873448785122164,0.4877989015663364]  |
|[2.6501218371679087,0.5756819768820428]  |
|[1.4965091203367626,-1.8644183183717817] |
|[3.9235207721573238,-0.2851835002352867] |
|[4.6110111098311135,0.6783790472312343]  |
|[2.8376900630842297,0.5712993716580531]  |
|[2.7066901398927827,1.2593788079708268]  |
|[4.698331383924287,-1.2765569680619442]  |
|[3.3759874966798673,-0.7560741064307506] |
|[5.608998877066021,-1.042731164439324]   |
|[-0.2954946352117681,0.27638645862362693]|
|[2.5725591062870423,1.3169815431109755]  |
|[3.400822802049345,-0.5073029625781933]  |
|[4.366720316263418,0.3364827059771049]   |
|[2.7254698167724003,-0.5058604987046399] |
|[4.958112358381604,-1.2627579957290722]  |
|[3.6934951846422712,-1.38227620

In [45]:
from pyspark.ml.clustering import KMeans

In [46]:
SEED = 1224

In [47]:
kmeans = KMeans(featuresCol='pca_features',
                predictionCol='cluster_pca').setK(5).setSeed(SEED)

In [48]:
model_kmeans = kmeans.fit(dados_generos_pca)

In [49]:
predictions_kmeans = model_kmeans.transform(dados_generos_pca)

In [50]:
predictions_kmeans.select('pca_features', 'cluster_pca').show(truncate=False)

+-----------------------------------------+-----------+
|pca_features                             |cluster_pca|
+-----------------------------------------+-----------+
|[-2.507095366888566,-0.43816913737698426]|2          |
|[0.5969679056633481,-4.9816120527513545] |2          |
|[4.158460276223561,0.8366525081079923]   |4          |
|[2.3873448785122164,0.4877989015663364]  |0          |
|[2.6501218371679087,0.5756819768820428]  |0          |
|[1.4965091203367626,-1.8644183183717817] |2          |
|[3.9235207721573238,-0.2851835002352867] |4          |
|[4.6110111098311135,0.6783790472312343]  |1          |
|[2.8376900630842297,0.5712993716580531]  |4          |
|[2.7066901398927827,1.2593788079708268]  |0          |
|[4.698331383924287,-1.2765569680619442]  |3          |
|[3.3759874966798673,-0.7560741064307506] |4          |
|[5.608998877066021,-1.042731164439324]   |1          |
|[-0.2954946352117681,0.27638645862362693]|2          |
|[2.5725591062870423,1.3169815431109755]  |0    

In [51]:
from pyspark.ml.functions import vector_to_array

In [52]:
pca_features_xy = predictions_kmeans.withColumn('x', vector_to_array('pca_features')[0])\
                  .withColumn('y', vector_to_array('pca_features')[1])\
                  .select(['x', 'y', 'cluster_pca', 'genres'])

In [53]:
pca_features_xy.show()

+-------------------+--------------------+-----------+--------------------+
|                  x|                   y|cluster_pca|              genres|
+-------------------+--------------------+-----------+--------------------+
| -2.507095366888566|-0.43816913737698426|          2|21st century clas...|
| 0.5969679056633481| -4.9816120527513545|          2|               432hz|
|  4.158460276223561|  0.8366525081079923|          4|               8-bit|
| 2.3873448785122164|  0.4877989015663364|          0|                  []|
| 2.6501218371679087|  0.5756819768820428|          0|          a cappella|
| 1.4965091203367626| -1.8644183183717817|          2|            abstract|
| 3.9235207721573238| -0.2851835002352867|          4|      abstract beats|
| 4.6110111098311135|  0.6783790472312343|          1|    abstract hip hop|
| 2.8376900630842297|  0.5712993716580531|          4|           accordeon|
| 2.7066901398927827|  1.2593788079708268|          0|           accordion|
|  4.6983313

In [54]:
fig = px.scatter(pca_features_xy.toPandas(),
                 x='x', y='y', color='cluster_pca',
                hover_data=['x','y', 'genres'])
fig.show()

In [55]:
pca_pipeline_model.stages[2].explainedVariance

DenseVector([0.2975, 0.1212])

   # Proposta de solucao

In [56]:
# Na definição da função vamos incluir os parâmetros que gostariamos de variar, como quantidade componentes, 
# número de clusters e colunas utilizadas 
def cria_pipeline(k_PCA=2, SEED=1224, k_kmeans=5, columns=x, data=dados_generos):

    #Definição do Pipeline 
    #Primeiro a vetorização das colunas selecionadas 
    #Segundo a padronização dos dados com o StandardScaler 
    #Terceiro o PCA com o número k_PCA de componentes 
    #Quarto o KMeans com o número k_kmeans de clusters 

    pca_pipeline = Pipeline(stages=[VectorAssembler(inputCols = columns, outputCol = 'features'),
                            StandardScaler(inputCol='features', outputCol='scaled_features'),
                            PCA(k=k_PCA, inputCol="scaled_features", outputCol='pca_features'),
                            KMeans(featuresCol='pca_features', predictionCol='cluster_pca', seed=SEED, k=k_kmeans)])

    #ajuste da pipeline com os dados 
    model = pca_pipeline.fit(data)

    #transformação dos dados utilizando o modelo da pipeline 
    predictions_kmeans = model.transform(data)

    #criando duas novas colunas a partir das primeiras duas componentes do PCA 

    pca_features_xs = predictions_kmeans\
    .withColumn("x", vector_to_array("pca_features")[0])\
    .withColumn("y", vector_to_array("pca_features")[1])\
    .select(['x', 'y', 'cluster_pca', 'genres'])

    #plotando as duas componentes e o cluster 
    fig = px.scatter( pca_features_xs.toPandas(), x='x', y='y', 
                     color='cluster_pca', 
                     hover_data=['x', 'y', 'genres']) 
    fig.show()

    #retornando pipeline ajustado 
    return model

In [57]:
cria_pipeline()

PipelineModel_1dd45816f6a6

In [58]:
display(dados.toPandas())

valence  year  acousticness        artists  danceability  duration_ms  \
0        0.285  2000       0.00239       Coldplay         0.429       266773   
1        0.613  2000       0.14300        OutKast         0.843       270507   
2        0.400  2000       0.00958    Linkin Park         0.556       216880   
3        0.543  2000       0.00664   3 Doors Down         0.545       233933   
4        0.760  2000       0.03020         Eminem         0.949       284200   
...        ...   ...           ...            ...           ...          ...   
20306    0.187  2020       0.57400          Bazzi         0.445       176250   
20307    0.240  2020       0.81500  Bryson Tiller         0.467       179188   
20308    0.466  2020       0.31000    Fleet Foxes         0.562       253613   
20309    0.522  2020       0.20400          Gunna         0.598       230600   
20310    0.195  2020       0.00998         Eminem         0.671       337147   

       energy  explicit                      id  instrumentalness  key  \
0       0.661         0  3AJwUDP919kvQ9QcozQPxg          0.000121   11   
1       0.806         1  0I3q5fE6wg7LIfHGngUTnV          0.000000    4   
2       0.864         0  60a0Rd6pjrkxjPbaKzXjfq          0.000000    3   
3       0.865         0  6ZOBP3NvffbU4SZcrnt1k6          0.000011   11   
4       0.661         1  3yfqSUWxFvZELEM4PmlwIR          0.000000    5   
...       ...       ...                     ...               ...  ...   
20306   0.330         0  0PUkanqCGTb6qseXPKOw1F          0.000000    9   
20307   0.429         0  6Iw6fQVKZi0fWtEQBrTFcP          0.000052    6   
20308   0.686         0  308prODCCD0O660tIktbUi          0.022500    7   
20309   0.472         1  2f8y4CuG57UJEmkG3ujd0D          0.000015    0   
20310   0.623         1  5SiZJoLXp3WOl3J4C8IK0d          0.000008    2   

       liveness  loudness  mode                    name  popularity  \
0        0.2340    -7.227     1                  Yellow          84   
1        0.0771    -5.946     0             Ms. Jackson          80   
2        0.2090    -5.870     0              In the End          84   
3        0.1680    -5.708     0              Kryptonite          78   
4        0.0454    -4.244     0     The Real Slim Shady          80   
...         ...       ...   ...                     ...         ...   
20306    0.1020    -8.121     1  I Don't Think I'm Okay          69   
20307    0.1770    -8.689     0      Timeless Interlude          65   
20308    0.1250    -8.480     1                Sunblind          66   
20309    0.1080   -10.991     1  NASTY GIRL / ON CAMERA          66   
20310    0.6430    -7.161     1                Darkness          70   

       speechiness    tempo                        artists_song  
0           0.0281  173.372                   Coldplay - Yellow  
1           0.2690   94.948               OutKast - Ms. Jackson  
2           0.0584  105.143            Linkin Park - In the End  
3           0.0286   99.009           3 Doors Down - Kryptonite  
4           0.0572  104.504        Eminem - The Real Slim Shady  
...            ...      ...                                 ...  
20306       0.0429  128.025      Bazzi - I Don't Think I'm Okay  
20307       0.0964  148.530  Bryson Tiller - Timeless Interlude  
20308       0.0249  103.054              Fleet Foxes - Sunblind  
20309       0.2580  120.080      Gunna - NASTY GIRL / ON CAMERA  
20310       0.3080   75.055                   Eminem - Darkness  

[20311 rows x 19 columns]

In [59]:
X = dados.columns
X.remove('artists')
X.remove('id')
X.remove('name')
X.remove('artists_song')
x

['mode',
 'acousticness',
 'danceability',
 'duration_ms',
 'energy',
 'instrumentalness',
 'liveness',
 'loudness',
 'speechiness',
 'tempo',
 'valence',
 'popularity',
 'key']

In [60]:
dados_encoded_vector = VectorAssembler(inputCols=X,
                                      outputCol='features').transform(dados)

In [61]:
dados_encoded_vector.select('features').show(truncate=False, n=5)

+-------------------------------------------------------------------------------------------------------------------------+
|features                                                                                                                 |
+-------------------------------------------------------------------------------------------------------------------------+
|[0.285,2000.0,0.00239,0.429,266773.0,0.6609999999999999,0.0,1.21E-4,11.0,0.234,-7.227,1.0,84.0,0.0281,173.372]           |
|[0.613,2000.0,0.143,0.843,270507.0,0.8059999999999999,1.0,0.0,4.0,0.0771,-5.9460000000000015,0.0,80.0,0.269,94.948]      |
|[0.4,2000.0,0.00958,0.556,216880.0,0.8640000000000001,0.0,0.0,3.0,0.209,-5.87,0.0,84.0,0.0584,105.143]                   |
|[0.5429999999999999,2000.0,0.00664,0.545,233933.0,0.865,0.0,1.1E-5,11.0,0.168,-5.7079999999999975,0.0,78.0,0.0286,99.009]|
|[0.76,2000.0,0.0302,0.949,284200.0,0.6609999999999999,1.0,0.0,5.0,0.0454,-4.244,0.0,80.0,0.0572,104.504]                 |
+-------

In [62]:
scaler = StandardScaler(inputCol='features', outputCol='features_scaled')
model_scaler = scaler.fit(dados_encoded_vector)
dados_musicas_scaler = model_scaler.transform(dados_encoded_vector)

In [63]:
dados_musicas_scaler.select('features_scaled').show(truncate=False, n=5)

+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|features_scaled                                                                                                                                                                                                                                                               |
+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|[1.156596679221045,329.8170613984441,0.008403188822334736,2.5040545743834373,3.7858811737298526,2.980511298201045,0.0,6.070790766862789E-4,3.0696424994844875,1.4832857988766257,-1.

In [64]:
k = len(X)
k

15

In [65]:
pca = PCA(k=k, inputCol='features_scaled', outputCol='pca_features')
model_pca = pca.fit(dados_musicas_scaler)
dados_musicas_pca = model_pca.transform(dados_musicas_scaler)

In [66]:
sum(model_pca.explainedVariance) * 100

100.00000000000004

In [67]:
lista_valores = [sum(model_pca.explainedVariance[0:i+1]) for i in range(k)]
lista_valores

[0.21297354127107346,
 0.3459774162295507,
 0.43989805678254457,
 0.5267820578269105,
 0.6001038103117929,
 0.666571951365239,
 0.7282174213581728,
 0.7845103843321024,
 0.8350002357002615,
 0.8812446547406771,
 0.9151737562703051,
 0.9435370133056041,
 0.9699018569070164,
 0.9900947792885583,
 1.0000000000000004]

In [68]:
import numpy as np

In [69]:
k = sum(np.array(lista_valores) <= 0.7)
k

6

In [70]:
pca = PCA(k=k, inputCol='features_scaled', outputCol='pca_features')
model_pca = pca.fit(dados_musicas_scaler)
dados_musicas_pca_final = model_pca.transform(dados_musicas_scaler)

In [71]:
display(dados_musicas_pca_final.toPandas())

valence  year  acousticness        artists  danceability  duration_ms  \
0        0.285  2000       0.00239       Coldplay         0.429       266773   
1        0.613  2000       0.14300        OutKast         0.843       270507   
2        0.400  2000       0.00958    Linkin Park         0.556       216880   
3        0.543  2000       0.00664   3 Doors Down         0.545       233933   
4        0.760  2000       0.03020         Eminem         0.949       284200   
...        ...   ...           ...            ...           ...          ...   
20306    0.187  2020       0.57400          Bazzi         0.445       176250   
20307    0.240  2020       0.81500  Bryson Tiller         0.467       179188   
20308    0.466  2020       0.31000    Fleet Foxes         0.562       253613   
20309    0.522  2020       0.20400          Gunna         0.598       230600   
20310    0.195  2020       0.00998         Eminem         0.671       337147   

       energy  explicit                      id  instrumentalness  ...  \
0       0.661         0  3AJwUDP919kvQ9QcozQPxg          0.000121  ...   
1       0.806         1  0I3q5fE6wg7LIfHGngUTnV          0.000000  ...   
2       0.864         0  60a0Rd6pjrkxjPbaKzXjfq          0.000000  ...   
3       0.865         0  6ZOBP3NvffbU4SZcrnt1k6          0.000011  ...   
4       0.661         1  3yfqSUWxFvZELEM4PmlwIR          0.000000  ...   
...       ...       ...                     ...               ...  ...   
20306   0.330         0  0PUkanqCGTb6qseXPKOw1F          0.000000  ...   
20307   0.429         0  6Iw6fQVKZi0fWtEQBrTFcP          0.000052  ...   
20308   0.686         0  308prODCCD0O660tIktbUi          0.022500  ...   
20309   0.472         1  2f8y4CuG57UJEmkG3ujd0D          0.000015  ...   
20310   0.623         1  5SiZJoLXp3WOl3J4C8IK0d          0.000008  ...   

       loudness  mode                    name  popularity speechiness  \
0        -7.227     1                  Yellow          84      0.0281   
1        -5.946     0             Ms. Jackson          80      0.2690   
2        -5.870     0              In the End          84      0.0584   
3        -5.708     0              Kryptonite          78      0.0286   
4        -4.244     0     The Real Slim Shady          80      0.0572   
...         ...   ...                     ...         ...         ...   
20306    -8.121     1  I Don't Think I'm Okay          69      0.0429   
20307    -8.689     0      Timeless Interlude          65      0.0964   
20308    -8.480     1                Sunblind          66      0.0249   
20309   -10.991     1  NASTY GIRL / ON CAMERA          66      0.2580   
20310    -7.161     1                Darkness          70      0.3080   

         tempo                        artists_song  \
0      173.372                   Coldplay - Yellow   
1       94.948               OutKast - Ms. Jackson   
2      105.143            Linkin Park - In the End   
3       99.009           3 Doors Down - Kryptonite   
4      104.504        Eminem - The Real Slim Shady   
...        ...                                 ...   
20306  128.025      Bazzi - I Don't Think I'm Okay   
20307  148.530  Bryson Tiller - Timeless Interlude   
20308  103.054              Fleet Foxes - Sunblind   
20309  120.080      Gunna - NASTY GIRL / ON CAMERA   
20310   75.055                   Eminem - Darkness   

                                                features  \
0      [0.285, 2000.0, 0.00239, 0.429, 266773.0, 0.66...   
1      [0.613, 2000.0, 0.143, 0.843, 270507.0, 0.8059...   
2      [0.4, 2000.0, 0.00958, 0.556, 216880.0, 0.8640...   
3      [0.5429999999999999, 2000.0, 0.00664, 0.545, 2...   
4      [0.76, 2000.0, 0.0302, 0.949, 284200.0, 0.6609...   
...                                                  ...   
20306  [0.187, 2020.0, 0.574, 0.445, 176250.0, 0.33, ...   
20307  [0.24, 2020.0, 0.815, 0.467, 179188.0, 0.429, ...   
20308  [0.466, 2020.0, 0.31, 0.562, 253613.0, 0.68599...   
20309  [0.522, 2020.0, 0.204, 0

In [72]:
dados_musicas_pca_final.select('pca_features').show(truncate=False, n=5)

+-----------------------------------------------------------------------------------------------------------------------+
|pca_features                                                                                                           |
+-----------------------------------------------------------------------------------------------------------------------+
|[-34.71004464775706,-165.3684878490618,-11.163498729832531,-139.11374280854452,14.152192300931285,-6.254422223810332]  |
|[-36.49885762774909,-167.85185045616552,-10.729023248906778,-135.90435265671317,13.388401890587135,-3.9729807278308047]|
|[-35.46030091694059,-165.99633344577884,-11.361290348240804,-138.2427688124702,13.866654919305686,-4.342675920458655]  |
|[-35.56301325520586,-165.59515096480604,-11.460226007030595,-137.52095740570059,15.568542803922625,-4.542073725584207] |
|[-36.5455697490757,-167.3751250580248,-11.881276527235773,-136.27798590244,14.056847990344442,-3.5833901457791004]     |
+-----------------------

In [73]:
sum(model_pca.explainedVariance) * 100

66.6571951365239

In [74]:
pca_pipeline = Pipeline(stages=[
    VectorAssembler(inputCols=X, outputCol='features'),
    StandardScaler(inputCol='features', outputCol='features_scaled'),
    PCA(k=k, inputCol='features_scaled', outputCol='pca_features')
])

In [75]:
model_pca_pipeline = pca_pipeline.fit(dados)

In [76]:
projection = model_pca_pipeline.transform(dados)

In [77]:
projection.select('pca_features').show(truncate=False, n=5)

+-----------------------------------------------------------------------------------------------------------------------+
|pca_features                                                                                                           |
+-----------------------------------------------------------------------------------------------------------------------+
|[-34.71004464775706,-165.3684878490618,-11.163498729832531,-139.11374280854452,14.152192300931285,-6.254422223810332]  |
|[-36.49885762774909,-167.85185045616552,-10.729023248906778,-135.90435265671317,13.388401890587135,-3.9729807278308047]|
|[-35.46030091694059,-165.99633344577884,-11.361290348240804,-138.2427688124702,13.866654919305686,-4.342675920458655]  |
|[-35.56301325520586,-165.59515096480604,-11.460226007030595,-137.52095740570059,15.568542803922625,-4.542073725584207] |
|[-36.5455697490757,-167.3751250580248,-11.881276527235773,-136.27798590244,14.056847990344442,-3.5833901457791004]     |
+-----------------------

In [78]:
kmeans = KMeans(k=50, featuresCol='pca_features', predictionCol='cluster_pca', seed=SEED)

In [79]:
modelo_kmeans = kmeans.fit(projection)

In [80]:
projection_kmeans = modelo_kmeans.transform(projection)

In [81]:
projection_kmeans.select(['pca_features','cluster_pca']).show()

+--------------------+-----------+
|        pca_features|cluster_pca|
+--------------------+-----------+
|[-34.710044647757...|          8|
|[-36.498857627749...|          4|
|[-35.460300916940...|         35|
|[-35.563013255205...|         16|
|[-36.545569749075...|         34|
|[-36.713222290262...|         34|
|[-36.013246178822...|         34|
|[-36.542687712104...|         23|
|[-36.425249009784...|         16|
|[-35.872074915770...|         34|
|[-31.639065936568...|         44|
|[-35.661446890546...|         34|
|[-35.574542234850...|         32|
|[-36.022399748656...|         13|
|[-34.336941950985...|         35|
|[-35.096906055142...|         49|
|[-35.202423054032...|         38|
|[-34.942948671026...|         30|
|[-36.617404517517...|          4|
|[-34.296973387410...|          6|
+--------------------+-----------+
only showing top 20 rows



In [82]:
projection_kmeans = projection_kmeans.withColumn('x', vector_to_array('pca_features')[0])\
                                     .withColumn('y', vector_to_array('pca_features')[1])   

In [83]:
projection_kmeans.select(['x', 'y', 'cluster_pca', 'artists_song']).show()

+-------------------+-------------------+-----------+--------------------+
|                  x|                  y|cluster_pca|        artists_song|
+-------------------+-------------------+-----------+--------------------+
| -34.71004464775706| -165.3684878490618|          8|   Coldplay - Yellow|
| -36.49885762774909|-167.85185045616552|          4|OutKast - Ms. Jac...|
| -35.46030091694059|-165.99633344577884|         35|Linkin Park - In ...|
| -35.56301325520586|-165.59515096480604|         16|3 Doors Down - Kr...|
|  -36.5455697490757| -167.3751250580248|         34|Eminem - The Real...|
| -36.71322229026236|-166.48208483099705|         34|Disturbed - Down ...|
| -36.01324617882224|-166.63514920955342|         34| Nelly - Ride Wit Me|
|-36.542687712104936| -166.9792823483324|         23|       Eminem - Stan|
| -36.42524900978434|-165.10535006330755|         16|*NSYNC - Bye Bye Bye|
| -35.87207491577076|-166.03098838247914|         34|Britney Spears - ...|
|-31.639065936568784|-166

In [84]:
fig = px.scatter(projection_kmeans.toPandas(), x='x', y='y', color='cluster_pca', hover_data=['artists_song'])
fig.show()

In [85]:
nome_musica = 'Taylor Swift - Blank Space'

In [86]:
cluster = projection_kmeans.filter(projection_kmeans.artists_song == nome_musica)\
                           .select('cluster_pca')\
                           .collect()[0][0]
                            
cluster

3

In [87]:
musicas_recomendadas = projection_kmeans.filter(projection_kmeans.cluster_pca == cluster)\
                                        .select('artists_song', 'id', 'pca_features')
musicas_recomendadas.show()

+--------------------+--------------------+--------------------+
|        artists_song|                  id|        pca_features|
+--------------------+--------------------+--------------------+
|Usher - Yeah! (fe...|5rb9QrpfcKFHM1EUb...|[-36.050436933493...|
|Kelly Clarkson - ...|3xrn9i8zhNZsTtcoW...|[-35.191226411337...|
| Keyshia Cole - Love|0W4NhJhcqKCqEP2GI...|[-34.751332435196...|
|Mariah Carey - We...|3LmvfNUQtglbTryds...|[-35.144610288312...|
|Korn - Coming Undone|6p2liQLGoDaLXgND6...|[-35.272207170621...|
|Chris Brown - Yo ...|7DFnq8FYhHMCylykf...|[-35.112344117719...|
|  Aventura - Un Beso|1SaEt8dwTuLDzenUu...|[-34.134357732463...|
|Chris Brown - Say...|5F7IJrXD6Fa3EmqoY...|[-34.728839526520...|
|Red Hot Chili Pep...|10Nmj3JCNoMeBQ87u...|[-36.101793760083...|
|Craig Morgan - In...|0Ta3jOf8m9yCSWMVw...|[-35.227552248025...|
|Arctic Monkeys - ...|3geFzA6VBSNZUTmV3...|[-34.696049351615...|
|Arctic Monkeys - 505|58ge6dfP91o9oXMzq...|[-35.057671072817...|
|T-Pain - Buy U a ...|2aI

In [88]:
componentes_musica = musicas_recomendadas.filter(musicas_recomendadas.artists_song == nome_musica)\
                                         .select('pca_features').collect()[0][0]
componentes_musica

DenseVector([-35.461, -166.9658, -12.7925, -137.9457, 13.1234, -4.1374])

In [89]:
!pip install scipy

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.1.2 -> 24.1.2
[notice] To update, run: python3 -m pip install --upgrade pip


In [90]:
from scipy.spatial.distance import euclidean
from pyspark.sql.types import FloatType

In [91]:
def calcula_distancia(value):
    return euclidean(componentes_musica, value)

udf_calcula_distancia = f.udf(calcula_distancia, FloatType())

musicas_recomendadas_dist = musicas_recomendadas.withColumn('Dist', udf_calcula_distancia('pca_features'))

recomendadas = sessao_spark.createDataFrame(musicas_recomendadas_dist.sort("Dist").take(10))\
                           .select(['artists_song', 'id', 'Dist'])
recomendadas.show()

+--------------------+--------------------+-------------------+
|        artists_song|                  id|               Dist|
+--------------------+--------------------+-------------------+
|Taylor Swift - Bl...|1p80LdxRV74UKvL8g...|                0.0|
|Imagine Dragons -...|4uGY9CqDtGtaTTLg1...|0.37921473383903503|
|The All-American ...|6ihL9TjfRjadfEePz...| 0.6039153933525085|
|Darius Rucker - B...|36ISlLb12gKuCCVTY...| 0.6824935674667358|
|Old Dominion - Sn...|7I5fYc4qKJddht8Oz...| 0.7364036440849304|
|Dan + Shay - Noth...|4W38RXuQNuoTSwVsQ...| 0.7841535210609436|
|Twenty One Pilots...|7qxjGHW485TL8ciwk...| 0.8002141118049622|
|Jon Bellion - Mor...|2JXNOtb0ANe6MzgRY...| 0.8098159432411194|
|Kip Moore - More ...|73WWkaWkIRSP3MYGZ...| 0.8557121753692627|
|Calibre 50 - Corr...|0ehx1p1HMn7NMKisZ...| 0.8788507580757141|
+--------------------+--------------------+-------------------+



In [92]:
def recomendador(nome_musica):
    cluster = projection_kmeans.filter(projection_kmeans.artists_song == nome_musica)\
                               .select('cluster_pca')\
                               .collect()[0][0]
    musicas_recomendadas = projection_kmeans.filter(projection_kmeans.cluster_pca == cluster)\
                                            .select('artists_song', 'id', 'pca_features')
    componentes_musica = musicas_recomendadas.filter(musicas_recomendadas.artists_song == nome_musica)\
                                             .select('pca_features').collect()[0][0]
    def calcula_distancia(value):
        return euclidean(componentes_musica, value)

    udf_calcula_distancia = f.udf(calcula_distancia, FloatType())

    musicas_recomendadas_dist = musicas_recomendadas.withColumn('Dist', udf_calcula_distancia('pca_features'))

    recomendadas = sessao_spark.createDataFrame(musicas_recomendadas_dist.sort("Dist").take(10))\
                               .select(['artists_song', 'id', 'Dist'])
    recomendadas.select('artists_song').show(truncate=False)

In [93]:
recomendador('Taylor Swift - Blank Space')

+-----------------------------------------+
|artists_song                             |
+-----------------------------------------+
|Taylor Swift - Blank Space               |
|Imagine Dragons - Machine                |
|The All-American Rejects - Gives You Hell|
|Darius Rucker - Beers And Sunshine       |
|Old Dominion - Snapback                  |
|Dan + Shay - Nothin' Like You            |
|Twenty One Pilots - Not Today            |
|Jon Bellion - Morning In America         |
|Kip Moore - More Girls Like You          |
|Calibre 50 - Corrido De Juanito          |
+-----------------------------------------+



In [94]:
def encontra_musica(nome_musica, projection_kmeans):
  resultado = projection_kmeans.filter(projection_kmeans.artists_song == nome_musica).collect()
  if len(resultado) == 0:
    return False
  return True

In [95]:
!pip install spotipy

Defaulting to user installation because normal site-packages is not writeable

[notice] A new release of pip is available: 23.1.2 -> 24.1.2
[notice] To update, run: python3 -m pip install --upgrade pip


In [96]:
import spotipy
from spotipy.oauth2 import SpotifyOAuth, SpotifyClientCredentials

In [97]:
scope = "user-library-read playlist-modify-private"

OAuth = SpotifyOAuth(
        scope=scope,         
        redirect_uri='http://localhost:5000/callback',
        client_id = 'dfa2695f82b34a2292f2e8e46e89a7c5',
        client_secret = '9001b3edfa214289acebcabd82e874b3')


In [98]:
client_credentials_manager = SpotifyClientCredentials(client_id = 'dfa2695f82b34a2292f2e8e46e89a7c5',
                                                      client_secret = '9001b3edfa214289acebcabd82e874b3')

sp = spotipy.Spotify(client_credentials_manager = client_credentials_manager)


In [99]:
id = projection_kmeans.filter(projection_kmeans.artists_song == nome_musica)\
                           .select('id')\
                           .collect()[0][0]
id

'1p80LdxRV74UKvL8gnD7ky'

In [100]:
sp.track(id)

{'album': {'album_type': 'album',
  'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/06HL4z0CvFAxyc27GXpf02'},
    'href': 'https://api.spotify.com/v1/artists/06HL4z0CvFAxyc27GXpf02',
    'id': '06HL4z0CvFAxyc27GXpf02',
    'name': 'Taylor Swift',
    'type': 'artist',
    'uri': 'spotify:artist:06HL4z0CvFAxyc27GXpf02'}],
  'available_markets': ['CA', 'US'],
  'external_urls': {'spotify': 'https://open.spotify.com/album/2QJmrSgbdM35R67eoGQo4j'},
  'href': 'https://api.spotify.com/v1/albums/2QJmrSgbdM35R67eoGQo4j',
  'id': '2QJmrSgbdM35R67eoGQo4j',
  'images': [{'height': 640,
    'url': 'https://i.scdn.co/image/ab67616d0000b2739abdf14e6058bd3903686148',
    'width': 640},
   {'height': 300,
    'url': 'https://i.scdn.co/image/ab67616d00001e029abdf14e6058bd3903686148',
    'width': 300},
   {'height': 64,
    'url': 'https://i.scdn.co/image/ab67616d000048519abdf14e6058bd3903686148',
    'width': 64}],
  'name': '1989',
  'release_date': '2014-10-27',
  'release

In [101]:
def recomendador(nome_musica):
    # Calcula musicas recomendadas
    cluster = projection_kmeans.filter(projection_kmeans.artists_song == nome_musica)\
                               .select('cluster_pca')\
                               .collect()[0][0]
    musicas_recomendadas = projection_kmeans.filter(projection_kmeans.cluster_pca == cluster)\
                                            .select('artists_song', 'id', 'pca_features')
    componentes_musica = musicas_recomendadas.filter(musicas_recomendadas.artists_song == nome_musica)\
                                             .select('pca_features').collect()[0][0]
    def calcula_distancia(value):
        return euclidean(componentes_musica, value)

    udf_calcula_distancia = f.udf(calcula_distancia, FloatType())

    musicas_recomendadas_dist = musicas_recomendadas.withColumn('Dist', udf_calcula_distancia('pca_features'))

    recomendadas = sessao_spark.createDataFrame(musicas_recomendadas_dist.sort("Dist").take(10))\
                               .select(['artists_song', 'id', 'Dist'])
    recomendadas.select('artists_song').show(truncate=False)
    
    #Pegar informacoes da API
    palylist_id = recomendadas.select('id').collect()
    
    playlist_track = []
    for i in palylist_id:
        playlist_track.append(sp.track(id[0]))
        
    return len(playlist_track)

In [102]:
recomendador('Taylor Swift - Blank Space')

+-----------------------------------------+
|artists_song                             |
+-----------------------------------------+
|Taylor Swift - Blank Space               |
|Imagine Dragons - Machine                |
|The All-American Rejects - Gives You Hell|
|Darius Rucker - Beers And Sunshine       |
|Old Dominion - Snapback                  |
|Dan + Shay - Nothin' Like You            |
|Twenty One Pilots - Not Today            |
|Jon Bellion - Morning In America         |
|Kip Moore - More Girls Like You          |
|Calibre 50 - Corrido De Juanito          |
+-----------------------------------------+



ERROR:spotipy.client:HTTP Error for GET to https://api.spotify.com/v1/tracks/1 with Params: {'market': None} returned 400 due to invalid id


SpotifyException: http status: 400, code:-1 - https://api.spotify.com/v1/tracks/1:
 invalid id, reason: None

In [ ]:
!pip install matplotlib
!pip install scikit-image

In [ ]:
import matplotlib.pyplot as plt
from skimage import io

nome_musica = 'Taylor Swift - Blank Space'

id = projection_kmeans\
          .filter(projection_kmeans.artists_song == nome_musica)\
          .select('id').collect()[0][0]

track = sp.track(id)

url = track["album"]["images"][1]["url"]
name = track["name"]

image = io.imread(url)
plt.imshow(image)
plt.xlabel(name, fontsize = 10)
plt.show()


In [ ]:
def visualize_songs(name,url):

    plt.figure(figsize=(15,10))
    columns = 5
    for i, u in enumerate(url):
        ax = plt.subplot(len(url) // columns + 1, columns, i + 1)
        image = io.imread(u)
        plt.imshow(image)
        ax.get_yaxis().set_visible(False)
        plt.xticks(color = 'w', fontsize = 0.1)
        plt.yticks(color = 'w', fontsize = 0.1)
        plt.xlabel(name[i], fontsize = 10)
        plt.tight_layout(h_pad=0.7, w_pad=0)
        plt.subplots_adjust(wspace=None, hspace=None)
        plt.grid(visible=None)
        #plt.axis('off')
    plt.show()

In [ ]:
playlist_id = recomendadas.select('id').collect()

name = []
url = []
for i in playlist_id:
    track = sp.track(i[0])
    url.append(track["album"]["images"][1]["url"])
    name.append(track["name"])


In [ ]:
visualize_songs(name,url)

In [ ]:
def recomendador(nome_musica):
 #Calcula musicas recomendadas
  cluster = projection_kmeans.filter(projection_kmeans.artists_song == nome_musica).select('cluster_pca').collect()[0][0]
  musicas_recomendadas = projection_kmeans.filter(projection_kmeans.cluster_pca == cluster)\
                                       .select('artists_song', 'id', 'pca_features')
  componenetes_musica = musicas_recomendadas.filter(musicas_recomendadas.artists_song == nome_musica)\
                                          .select('pca_features').collect()[0][0]

  def calcula_distance(value):
    return euclidean(componenetes_musica, value)

  udf_calcula_distance = f.udf(calcula_distance, FloatType())

  musicas_recomendadas_dist = musicas_recomendadas.withColumn('Dist', udf_calcula_distance('pca_features'))

  recomendadas = sessao_spark.createDataFrame(musicas_recomendadas_dist.sort('Dist').take(10)).select(['artists_song', 'id', 'Dist'])

  #Pegar informações da API

  playlist_id = recomendadas.select('id').collect()

  name = []
  url = []
  for i in playlist_id:
      track = sp.track(i[0])
      url.append(track["album"]["images"][1]["url"])
      name.append(track["name"])

  #Plotando capas 

  plt.figure(figsize=(15,10))
  columns = 5
  for i, u in enumerate(url):
      ax = plt.subplot(len(url) // columns + 1, columns, i + 1)
      image = io.imread(u)
      plt.imshow(image)
      ax.get_yaxis().set_visible(False)
      plt.xticks(color = 'w', fontsize = 0.1)
      plt.yticks(color = 'w', fontsize = 0.1)
      plt.xlabel(name[i], fontsize = 10)
      plt.tight_layout(h_pad=0.7, w_pad=0)
      plt.subplots_adjust(wspace=None, hspace=None)
      plt.grid(visible=None)
      #plt.axis('off')
  plt.show()


In [ ]:
recomendador('Taylor Swift - Blank Space')
